
### Работа с полигональными моделями и облаками точек. MeshLab / `pymeshlab`

Полигональная/фасетная модель (меш) это набор многоугольников, обычно треугольников. Задается в виде списка точек (которые задаются в виде списка координат) и еще троек.

На данные, что на входные, что на выходные, очень полезно смотреть глазами.

С картинками, текстами и аудио это делается тривиально.

Рассмотрим, как это делается с 3D данными.


[Download MeshLab GUI](https://www.meshlab.net/#download)

< Секция с демонстрацией открытия меша, семплингом, подсчетом метрик >

In [1]:
# !pip install open3d
# !pip install pymeshlab
# !pip install --upgrade PyMCubes
# !pip install edt
# !pip install mesh2sdf

### Что происходит внутри

In [2]:
w = 320
h = 200

<table align='left'>
<tr>
<td><img src='imgs/mesh.png' width=str(w) height=str(h)/></td>
<td><img src='imgs/pc.png' width=str(w) height=str(h)/></td>
<td><img src='imgs/m.png' width=str(w) height=str(h)/></td>
</tr>

<table align='left'>
<tr>
<td><img src='imgs/metric.png' width=str(w) height=str(h)/></td>
<td><img src='imgs/geo.png' width=str(w) height=str(h)/></td>
</tr>


</table>

### Как то же самое сделать программно

In [ ]:
import numpy as np
import open3d as o3d
import pymeshlab as pml
import matplotlib.pyplot as plt

In [4]:
# "Легкая" Визуализация удобнее в Open3D

armadillo_mesh = o3d.data.ArmadilloMesh() # скачиваем из интернета мешфайл
path = armadillo_mesh.path

# path = 'armadillo.obj'
mesh = o3d.io.read_triangle_mesh(path)
mesh.compute_vertex_normals()
o3d.visualization.draw_geometries([mesh])

In [5]:
## Вычисления/Операции над мешами делаются в MeshLab

ms = pml.MeshSet() # создаем мешсет
ms.load_new_mesh(path)
#https://pymeshlab.readthedocs.io/en/latest/filter_list.html#generate_sampling_poisson_disk
ms.generate_sampling_poisson_disk(samplenum = 10000) # создается объект ms[1], в котором только вершины
ms.generate_surface_reconstruction_screened_poisson() # создается объект ms[2], это меш
ms.compute_scalar_by_distance_from_another_mesh_per_vertex(measuremesh=0, refmesh=2)

In [ ]:
scalar_np = ms[0].vertex_scalar_array()
print('per-vertex scalar values are:', scalar_np)
vertices_np = ms[0].vertex_matrix()

In [7]:
def normalize_array(arr:np.array):
    '''     remaps any array to [0,1]    '''
    L = arr.max() - arr.min()
    return (arr - arr.min()) / L

In [8]:
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(vertices_np)
normalized = normalize_array(scalar_np)
cmap = plt.cm.RdBu
colors = cmap(normalized)[:,:3]
pcd.colors = o3d.utility.Vector3dVector(colors)

# открывается отдельное окно
o3d.visualization.draw_geometries([pcd])

### Signed Distance Function
Определение в стиле Computer Science / Computer Graphics

\begin{equation}
    SDF(x) = \left\{\begin{array}{rl}
        dist(x, \partial\Omega), &\textrm{если $x$ снаружи объекта } \Omega, \\
        -dist(x, \partial\Omega), &\textrm{иначе,} \\
    \end{array}\right.
\end{equation}


Определение в стиле математики
\begin{equation}
\begin{array}{rl}
    | \nabla u(x)| &= 1, x \in \mathbb{R}^3 \\
    u|_{\partial \Omega} &= 0 \\
    u(x) >0 &\textrm{если $x$ снаружи объекта }
\end{array}\
\end{equation}

(Сайт для доп. изучения)(https://iquilezles.org/articles/distfunctions/)

Также важное понятие:


Усечённая знаковая функция расстояния (Truncated Signed Distance Function)
\begin{equation}
    TSDF(p) = \left\{\begin{array}{rl}
        \mu, &\textrm{if } \mu \leq SDF(p) \\
        SDF(p), &\textrm{if } -\mu < SDF(p) < \mu \\
        -\mu, &\textrm{if } SDF(p) \leq -\mu. \\
    \end{array}\right.
\end{equation}



1. Исторически важные статьи TSDF Fusion и KinectFusion
SOTA донейронной эпохи. Работает в реальном времени на GPU времен 2010г.
Идея была такая, что по карте глубины можно по формуле считать "проективный SDF", который (примерно) верен вблизи поверхности. Если поснимать объект сразных сторон и усреднить, вблизи поверхности получается очень близко к настоящему SDF. Но нужно обрезать результат в окрестности от поверхности, чтобы не начать ловить артефакты.

2. В современной литературе даже когда слова Truncated нет в названии, в статье де-факто используется именно TSDF.

"Честный" SDF можно получить *только* 

- для фигур, для которых он известен аналитически (в том числе для меш, но это затратно)
- честным решателем уравнения эйконала, таким как ```edt``` (есть методы быстрее чем N^3)
- через фитинг эйконал-лосса на нейронную сеть или еще куда

$$L = (\left| \nabla u_\theta(x) \right| -1 )^2$$

## 2D SDF

<table align='left'>
    <tr>
    <img src='imgs/sdf2d.jpg' width=440 height=str(h)/>
    <img src='imgs/sdf4.png' width=440 height=str(h)/>
    </tr>
    <table align='left'>
</table>

<table align='left'>
    <tr>
    <td><img src='imgs/u1.png' width=str(w) height=str(h)/></td>
</table>

## 3D SDF

ModelNet plane-0629 (watertight version), SDF, TSDF (normalized)

<table align='left'>
    <tr>
    <img src='imgs/dat_plane00s.png' width=440 height=str(h)/>
    </tr>
    <tr>
    <img src='imgs/sdf_full.png' width=str(w) height=str(h)/>
    </tr>
    <tr>
    <img src='imgs/tsdf_full.png' width=str(w) height=str(h)/>
    </tr>
</table>

In [9]:
import mcubes
import edt

In [10]:
N = 128
x, y, z = np.mgrid[:N, :N, :N]

binary_sphere = (x - N//2)**2 + (y - N//2)**2 + (z - N//2)**2 - (N//4)**2 < 0
vertices, triangles = mcubes.marching_cubes(binary_sphere, 0.5) # 1 - binary_sphere to keep normals outwards
mcubes.export_obj(vertices, triangles, "sphere.obj", "MySphere")

smoothed_sphere = mcubes.smooth(binary_sphere)
vertices_smooth, triangles_smooth = mcubes.marching_cubes(smoothed_sphere, 0)
mcubes.export_obj(vertices_smooth, triangles_smooth, "sphere_smooth.obj", "MySphere")

In [ ]:
plt.imshow(binary_sphere[N//2,:,:])
plt.colorbar()

In [12]:
def sdf(x):
    return (1-x)*(edt.edt(1-x)-1) - edt.edt(x)*x

In [ ]:
sdf_data = sdf(binary_sphere)
vertices_sdf, triangles_sdf = mcubes.marching_cubes(sdf_data, 0)
mcubes.export_obj(vertices_sdf, triangles_sdf, "sphere_from_sdf.obj")

data = sdf_data[N//2, :, :]
plt.imshow(data)
plt.colorbar()
plt.contour(data, levels=[0], colors=['white'])

In [14]:
mesh = o3d.io.read_triangle_mesh('chair.obj')
mesh.compute_vertex_normals()
o3d.visualization.draw_geometries([mesh])

In [15]:
# [Open3D INFO]   -- Render mode control --
# [Open3D INFO]     L            : Turn on/off lighting.
# [Open3D INFO]     +/-          : Increase/decrease point size.
# [Open3D INFO]     Ctrl + +/-   : Increase/decrease width of geometry::LineSet.
# [Open3D INFO]     N            : Turn on/off point cloud normal rendering.
# [Open3D INFO]     S            : Toggle between mesh flat shading and smooth shading.
# [Open3D INFO]     W            : Turn on/off mesh wireframe.
# [Open3D INFO]     B            : Turn on/off back face rendering.
# [Open3D INFO]     I            : Turn on/off image zoom in interpolation.
# [Open3D INFO]     T            : Toggle among image render:
# [Open3D INFO]                    no stretch / keep ratio / freely stretch.
# [Open3D INFO]     Ctrl + 0..4,9: Set mesh color option.
# [Open3D INFO]                    0 - Default behavior, render uniform gray color.
# [Open3D INFO]                    1 - Render point color.
# [Open3D INFO]                    2 - x coordinate as color.
# [Open3D INFO]                    3 - y coordinate as color.
# [Open3D INFO]                    4 - z coordinate as color.
# [Open3D INFO]                    9 - normal as color.


In [16]:
import os
import sys
# import trimesh
import mesh2sdf

import time

filename = sys.argv[1] if len(sys.argv) > 1 else  \
    os.path.join(os.path.dirname(__file__), 'data', 'plane.obj')

mesh_scale = 0.8
size = 128
level = 2 / size

# mesh = trimesh.load('chair.obj')

# normalize mesh
vertices = np.asarray(mesh.vertices)
faces = np.asarray(mesh.triangles)
bbmin = vertices.min(0)
bbmax = vertices.max(0)
center = (bbmin + bbmax) * 0.5
scale = 2.0 * mesh_scale / (bbmax - bbmin).max()
vertices = (vertices - center) * scale

# fix mesh
t0 = time.time()
sdf, mesh = mesh2sdf.compute(
    vertices, faces, size, fix=True, level=level, return_mesh=True)
t1 = time.time()

In [ ]:
data = sdf[size//2, :, :]
plt.imshow(data)
plt.contour(data, levels=[0], colors=['white'])

Конверсия в бинарное:
Сам по себе набор треугольников не несет информации о том, лежит ли та или иная точка внутри или снаружи.

Старая техника получения сдф
1) из меша можно получить TSDF, рендеря карту глубины с разных камер.
2) TSDF будет очень хорошо аппроксимировать в окрестности поверхности
3) каким-нибудь точным солвером уравнения эйконала (воксельным) найти SDF, склеить их вместе

---
Курс "Трехмерное компьютерное зрение" в ШАД, А.Конушин и команда.
Семинар подготовил А.Бойко.